<a href="https://colab.research.google.com/github/NicolePrata/DiplomadoTareas/blob/main/FlightPrices_NicolePrata.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import pandas as pd
import numpy as np
import plotly.express as px
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.preprocessing import StandardScaler
#from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report, confusion_matrix


In [3]:
df=pd.read_csv('/content/flightprice2.csv')
df.head()

Unnamed: 0   airline   flight source_city departure_time stops  \
0           0  SpiceJet  SG-8709       Delhi        Evening  zero   
1           1  SpiceJet  SG-8157       Delhi  Early_Morning  zero   
2           2   AirAsia   I5-764       Delhi  Early_Morning  zero   
3           3   Vistara   UK-995       Delhi        Morning  zero   
4           4   Vistara   UK-963       Delhi        Morning  zero   

    arrival_time destination_city    class  duration  days_left   price  
0          Night           Mumbai  Economy      2.17        1.0  5953.0  
1        Morning           Mumbai  Economy      2.33        1.0  5953.0  
2  Early_Morning           Mumbai  Economy      2.17        1.0  5956.0  
3      Afternoon           Mumbai  Economy      2.25        1.0  5955.0  
4        Morning           Mumbai  Economy      2.33        1.0  5955.0

In [4]:
df = pd.DataFrame(df)
df

Unnamed: 0   airline   flight source_city departure_time stops  \
0                0  SpiceJet  SG-8709       Delhi        Evening  zero   
1                1  SpiceJet  SG-8157       Delhi  Early_Morning  zero   
2                2   AirAsia   I5-764       Delhi  Early_Morning  zero   
3                3   Vistara   UK-995       Delhi        Morning  zero   
4                4   Vistara   UK-963       Delhi        Morning  zero   
...            ...       ...      ...         ...            ...   ...   
290382      290382   Vistara   UK-836     Chennai        Morning   one   
290383      290383   Vistara   UK-832     Chennai  Early_Morning   one   
290384      290384   Vistara   UK-838     Chennai          Night   one   
290385      290385   Vistara   UK-832     Chennai  Early_Morning   one   
290386      290386   Vistara   UK-838     Chennai            NaN   NaN   

         arrival_time destination_city     class  duration  days_left    price  
0               Night           Mumbai   Economy      2.17        1.0   5953.0  
1             Morning           Mumbai   Economy      2.33        1.0   5953.0  
2       Early_Morning           Mumbai   Economy      2.17        1.0   5956.0  
3           Afternoon           Mumbai   Economy      2.25        1.0   5955.0  
4             Morning           Mumbai   Economy      2.33        1.0   5955.0  
...               ...              ...       ...       ...        ...      ...  
290382          Night           Mumbai  Business     10.50        2.0  80129.0  
290383          Night           Mumbai  Business     13.17        2.0  80129.0  
290384        Morning           Mumbai  Business     14.08        2.0  80129.0  
290385          Night           Mumbai  Business     14.33        2.0  80129.0  
290386            NaN              NaN       NaN       NaN        NaN      NaN  

[290387 rows x 12 columns]

In [5]:
#elimino valores NaN
df = df.dropna()
df.shape

(290386, 12)

In [6]:
df=df.drop('Unnamed: 0',axis=1)

# Análisis Exploratorio

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 290386 entries, 0 to 290385
Data columns (total 11 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   airline           290386 non-null  object 
 1   flight            290386 non-null  object 
 2   source_city       290386 non-null  object 
 3   departure_time    290386 non-null  object 
 4   stops             290386 non-null  object 
 5   arrival_time      290386 non-null  object 
 6   destination_city  290386 non-null  object 
 7   class             290386 non-null  object 
 8   duration          290386 non-null  float64
 9   days_left         290386 non-null  float64
 10  price             290386 non-null  float64
dtypes: float64(3), object(8)
memory usage: 26.6+ MB


In [8]:
df.describe()

duration      days_left          price
count  290386.000000  290386.000000  290386.000000
mean       12.126660      26.010589   19756.095821
std         7.196927      13.563697   22095.921291
min         0.830000       1.000000    1105.000000
25%         6.670000      15.000000    4697.000000
50%        11.170000      26.000000    7141.000000
75%        16.080000      38.000000   38043.000000
max        49.830000      49.000000  123071.000000

In [9]:
features = ['airline', 'source_city', 'destination_city', 'departure_time', 'arrival_time', 'stops', 'class']

for feature in features:
    print(f'{feature}:', df[feature].unique())

airline: ['SpiceJet' 'AirAsia' 'Vistara' 'GO_FIRST' 'Indigo' 'Air_India']
source_city: ['Delhi' 'Mumbai' 'Bangalore' 'Kolkata' 'Hyderabad' 'Chennai']
destination_city: ['Mumbai' 'Bangalore' 'Kolkata' 'Hyderabad' 'Chennai' 'Delhi']
departure_time: ['Evening' 'Early_Morning' 'Morning' 'Afternoon' 'Night' 'Late_Night']
arrival_time: ['Night' 'Morning' 'Early_Morning' 'Afternoon' 'Evening' 'Late_Night']
stops: ['zero' 'one' 'two_or_more']
class: ['Economy' 'Business']


In [10]:
fig = px.box(df, x='airline', y='price', title='Aerolínea y Precio',
             labels={'airline': 'Aerolínea', 'price': 'Precio'}, template='plotly_white')
fig.show()

Esto lo hice para poder pasar los valores object como las aerolíneas a valores numéricos para mi regresión

In [11]:
from sklearn.preprocessing import LabelEncoder
le=LabelEncoder()

In [12]:
for i in df.columns:
    if df[i].dtype == 'object':
        df[i]=le.fit_transform(df[i])

In [13]:
corr_matrix = df.corr()

fig = px.imshow(corr_matrix, color_continuous_scale = 'RdBu', range_color=[-1,1], text_auto = True, aspect = "auto", labels=dict(color="Correlation"), title='Feature Correlation', height = 800)
fig.update(layout_coloraxis_showscale=False)
fig.show()

In [14]:
X_train, X_test, y_train, y_test = train_test_split(df.drop(['price'],axis=1), df['price'], test_size=0.2, random_state=7)

In [15]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((232308, 10), (58078, 10), (232308,), (58078,))

In [16]:
X_train

airline  flight  source_city  departure_time  stops  arrival_time  \
28283         5    1441            2               1      2             4   
89071         1     858            0               1      2             4   
110769        5    1528            0               1      2             4   
224243        5    1489            2               2      2             5   
224878        5    1541            2               4      0             5   
...         ...     ...          ...             ...    ...           ...   
235075        1     817            5               1      0             0   
10742         4    1360            2               5      2             3   
49689         2    1037            5               0      2             0   
189636        5    1490            1               4      0             5   
61615         3     321            5               1      0             0   

        destination_city  class  duration  days_left  
28283                  4      1      2.08       47.0  
89071                  2      1      3.00       26.0  
110769                 3      1      1.17       12.0  
224243                 1      0      2.83       39.0  
224878                 1      0     11.42       48.0  
...                  ...    ...       ...        ...  
235075                 4      0      4.25       14.0  
10742                  0      1      2.75        6.0  
49689                  2      1      2.25       35.0  
189636                 5      1     10.00       18.0  
61615                  4      1      6.50        1.0  

[232308 rows x 10 columns]

In [17]:
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

In [18]:
def plot_confusion_matrix(cm, labels):
    fig_cm = px.imshow(cm, labels=dict(x="Predicted", y="Actual", color="Count"),
                       x=labels, y=labels, color_continuous_scale='Viridis', text_auto = True,
                       title="Confusion Matrix")
    fig_cm.update_layout(coloraxis_showscale=False)
    fig_cm.show()

## Regresión Logística

In [ ]:
from sklearn.linear_model import LogisticRegression
lr = LogisticRegression()
lr.fit(X_train_scaled, y_train)

In [ ]:
lr_pred = lr.predict(X_test_scaled)
lr_pred

In [ ]:
lr_accuracy = accuracy_score(y_test, lr_pred)
print(f"Logistic Regression Accuracy: {lr_accuracy:.2f}")

In [ ]:
lr_precision = precision_score(y_test, lr_pred)
print(f"Logistic Regression Precission: {lr_precision:.2f}")

In [ ]:
lr_recall = recall_score(y_test, lr_pred)
print(f"Logistic Regression Recall: {lr_recall:.2f}")

In [ ]:
lr_f1 = f1_score(y_test, lr_pred)
print(f"Logistic Regression F1 Score: {lr_f1:.2f}")

In [ ]:
lr_report = classification_report(y_test, lr_pred)
print("Logistic Regression Classification Report:")
print(lr_report)

In [ ]:
lr_cm = confusion_matrix(y_test, lr_pred)

#lr_cm

# K-Nearest Neighbors (KNN)

In [ ]:
knn = KNeighborsClassifier()
knn.fit(X_train_scaled, y_train)

In [ ]:
knn_pred = knn.predict(X_test_scaled)

In [ ]:
knn_accuracy = accuracy_score(y_test, knn_pred)
print(f"KNN Accuracy: {knn_accuracy:.2f}")

In [ ]:
knn_precision = precision_score(y_test, knn_pred)
print(f"KNN Precission: {knn_precision:.2f}")

In [ ]:
knn_recall = recall_score(y_test, knn_pred)
print(f"KNN Recall: {knn_recall:.2f}")

In [ ]:
knn_f1 = f1_score(y_test, knn_pred)
print(f"KNN F1 Score: {knn_f1:.2f}")

# Support Vector Machines (SVM)

In [ ]:
svm = SVC()
svm.fit(X_train_scaled, y_train)

In [ ]:
svm_pred = svm.predict(X_test_scaled)

In [ ]:
svm_accuracy = accuracy_score(y_test, svm_pred)
print(f"SVM Accuracy: {svm_accuracy:.2f}")

In [ ]:
svm_precision = precision_score(y_test, svm_pred)
print(f"SVM Precission: {svm_precision:.2f}")

In [ ]:
svm_recall = recall_score(y_test, svm_pred)
print(f"KNN Recall: {svm_recall:.2f}")

In [ ]:
svm_f1 = f1_score(y_test, svm_pred)
print(f"SVM F1 Score: {svm_f1:.2f}")

In [ ]:
svm_report = classification_report(y_test, svm_pred)
print("SVM Classification Report:")
print(svm_report)

# Naive Bayes

# Decision Tree



In [ ]:
dt = DecisionTreeClassifier()
dt.fit(X_train_scaled, y_train)

In [ ]:
dt_pred = dt.predict(X_test_scaled)

In [ ]:
dt_accuracy = accuracy_score(y_test, dt_pred)
print(f"Decision Trees Accuracy: {dt_accuracy:.2f}")

In [ ]:
dt_precision = precision_score(y_test, dt_pred)
print(f"Decision Trees Precission: {dt_precision:.2f}")

In [ ]:
dt_recall = recall_score(y_test, dt_pred)
print(f"Decision Trees Recall: {dt_recall:.2f}")

In [ ]:
dt_f1 = f1_score(y_test, dt_pred)
print(f"Decision Trees F1 Score: {dt_f1:.2f}")

In [ ]:
dt_report = classification_report(y_test, dt_pred)
print("Decision Trees Classification Report:")
print(dt_report)

# Random Forest

In [ ]:
rf = RandomForestClassifier()
rf.fit(X_train_scaled, y_train)

In [ ]:
rf_pred = rf.predict(X_test_scaled)

In [ ]:
rf_accuracy = accuracy_score(y_test, rf_pred)
print(f"Random Forest Accuracy: {rf_accuracy:.2f}")

In [ ]:
rf_precision = precision_score(y_test, rf_pred)
print(f"Random Forest Precission: {rf_precision:.2f}")

In [ ]:
rf_recall = recall_score(y_test, rf_pred)
print(f"Random Forest Recall: {rf_recall:.2f}")

In [ ]:
rf_f1 = f1_score(y_test, rf_pred)
print(f"Random Forest F1 Score: {rf_f1:.2f}")

In [ ]:
rf_report = classification_report(y_test, rf_pred)
print("Random Forest Classification Report:")
print(rf_report)